In [148]:
import os
import json
import pandas as pd
import random
import numpy as np
from collections import Counter

In [149]:
def count_card_occurrences(card_df: pd.DataFrame, deck_dir: str = "data/decks"):
    card_occurrences = {}

    deck_files = os.listdir(deck_dir)
    deck_json_files = [file for file in deck_files if file.endswith(".json")]

    for deck_file in deck_json_files:
        with open(os.path.join(deck_dir, deck_file), "r") as file:
            deck_data = json.load(file)

        for card in deck_data["Cards"]:
            card_id = card["id"]
            card_occurrences[card_id] = card_occurrences.get(card_id, 0) + 1

    max_occurrence = max(card_occurrences.values(), default=1)

    return card_occurrences


def print_top_occurring_cards(card_occurrences: dict, card_df: pd.DataFrame, top_n=20):
    sorted_card_occurrences = sorted(card_occurrences.items(), key=lambda x: x[1], reverse=True)

    print(f"Top {top_n} Most Occurring Cards:")
    for idx, (card_id, count) in enumerate(sorted_card_occurrences[:top_n], 1):
        card_name = card_df.loc[card_id, "name"]
        print(f"{idx}. {card_name}: {count} times")


In [171]:
card_df = pd.read_csv("data/card_database.csv")
card_df.set_index('id', inplace=True)

card_occurrences = count_card_occurrences(card_df)

top_occurring = max(card_occurrences.items(), key=lambda x: x[1])
print(card_df.loc[top_occurring[0], "name"], top_occurring[1])

import numpy as np

normalized_occurrences = {
    card: np.log(1 + count) / np.log(1 + top_occurring[1])
    for card, count in card_occurrences.items()
}

print_top_occurring_cards(card_occurrences, card_df, top_n=2000)

Oneiromancy 305
Top 2000 Most Occurring Cards:
1. Oneiromancy: 305 times
2. Royal Decree: 238 times
3. Korathi Heatwave: 224 times
4. Squirrel: 129 times
5. Roach: 115 times
6. Spores: 112 times
7. Vial of Forbidden Knowledge: 106 times
8. Imperial Diplomacy: 102 times
9. Knickers: 101 times
10. Megascope: 100 times
11. Lord Riptide: 98 times
12. Golden Nekker: 93 times
13. Tourney Joust: 90 times
14. Amphibious Assault: 82 times
15. Pellar: 82 times
16. Buhurt: 80 times
17. Call of the Forest: 77 times
18. Artorius Vigo: 77 times
19. Ciri: Nova: 77 times
20. Freya's Blessing: 76 times
21. Mage Assassin: 71 times
22. Coup de Grace: 71 times
23. Operator: 70 times
24. Menno Coehoorn: 66 times
25. Vilgefortz: 65 times
26. Mahakam Ale: 64 times
27. Fucusya: 61 times
28. Dorregaray of Vole: 61 times
29. Van Moorlehem Hunter: 61 times
30. Blightmaker: 60 times
31. Seagull: 60 times
32. Avallac'h: Sage: 59 times
33. Battle Stations!: 59 times
34. Vivaldi Bank: 57 times
35. War Council: 57 ti

In [151]:
def generate_card_cooccurrence_matrix(card_frequency, deck_dir: str = "data/decks"):
    """
    Generates a co-occurrence matrix of cards based on decks in the specified directory.
    Divides the co-occurrence counts by the frequency of the most frequent card.

    Args:
        card_df (pd.DataFrame): A DataFrame containing card metadata, indexed by card ID.
        deck_dir (str): Directory containing deck JSON files.

    Returns:
        np.ndarray: A co-occurrence matrix where each entry (i, j) represents the co-occurrence 
                    count of card i and card j across all decks, normalized by card frequency.
    """
    card_cooccurrence = {}

    deck_files = os.listdir(deck_dir)
    deck_json_files = [file for file in deck_files if file.endswith(".json")]

    for deck_file in deck_json_files:
        with open(os.path.join(deck_dir, deck_file), "r") as file:
            deck_data = json.load(file)

        card_ids = [card["id"] for card in deck_data["Cards"]]

        for i in range(len(card_ids)):
            for j in range(i + 1, len(card_ids)):
                card_i, card_j = card_ids[i], card_ids[j]

                if card_i not in card_cooccurrence:
                    card_cooccurrence[card_i] = {}
                if card_j not in card_cooccurrence[card_i]:
                    card_cooccurrence[card_i][card_j] = 0
                card_cooccurrence[card_i][card_j] += 1

                if card_j not in card_cooccurrence:
                    card_cooccurrence[card_j] = {}
                if card_i not in card_cooccurrence[card_j]:
                    card_cooccurrence[card_j][card_i] = 0
                card_cooccurrence[card_j][card_i] += 1

    for card_i in card_cooccurrence:
        for card_j in card_cooccurrence[card_i]:
            card_cooccurrence[card_i][card_j] /= max(card_frequency.get(card_i, 1), card_frequency.get(card_j, 1)) 

    # Create a DataFrame from the dictionary
    cooccurrence_matrix = pd.DataFrame.from_dict(
        {card_id: pd.Series(card_cooccurrence.get(card_id, {})) for card_id in card_cooccurrence},
        orient='index'
    ).fillna(0)

    return cooccurrence_matrix


In [152]:
def print_top_cooccurring_pairs(cooccurrence_matrix: pd.DataFrame, card_df: pd.DataFrame, top_n=20):
    pairs = []
    for i in cooccurrence_matrix.columns:
        for j in cooccurrence_matrix.index:
            if i < j:  # Avoid duplicates (only consider i < j for uniqueness)
                count = cooccurrence_matrix.loc[j, i]  # Co-occurrence value at position (i, j)
                if count > 0:
                    pairs.append(((i, j), count))

    pairs.sort(key=lambda x: x[1], reverse=True)

    print(f"Top {top_n} Most Co-occurring Card Pairs:")
    for idx, ((card_id1, card_id2), count) in enumerate(pairs[:top_n], 1):
        card1_name = card_df.loc[card_id1, "name"]
        card2_name = card_df.loc[card_id2, "name"]
        print(f"{idx}. {card1_name} & {card2_name}: {count} times")


In [153]:
cooccurrence_matrix = generate_card_cooccurrence_matrix(card_occurrences)

print_top_cooccurring_pairs(cooccurrence_matrix, card_df, top_n=1000000000000000000000)

Top 1000000000000000000000 Most Co-occurring Card Pairs:
1. Eskel & Vesemir: 1.0 times
2. Eskel & Lambert: 1.0 times
3. Vesemir & Lambert: 1.0 times
4. Etriel & Muirlega: 1.0 times
5. Mahakam Guard & Brouver Hoog: 1.0 times
6. Unicorn & Chironex: 1.0 times
7. Aucwenn & Naiad Pondkeeper: 1.0 times
8. Aucwenn & Naiad Fledgling: 1.0 times
9. Naiad Pondkeeper & Naiad Fledgling: 1.0 times
10. Drummond Shieldmaiden & Cerys An Craite: 1.0 times
11. The Witchfinder & The Scoundrel: 1.0 times
12. The Witchfinder & The Brute: 1.0 times
13. The Scoundrel & The Brute: 1.0 times
14. Gan Ceann & Selfeater: 1.0 times
15. Arena Endrega & Greater Brothers: 1.0 times
16. Damned Sorceress & Immortals: 1.0 times
17. Ban Ard Student & Aretuza Student: 1.0 times
18. King Chrum & Cyclops Warrior: 1.0 times
19. In Search of Forgotten Treasures & Flyndr's Crew: 1.0 times
20. The Eternal Eclipse & Master of Ceremonies: 1.0 times
21. The Eternal Eclipse & Eternal Eclipse Deacon: 1.0 times
22. The Eternal Eclipse

In [154]:
def count_leader_abilities_and_stratagems(deck_dir: str = "data/decks"):
    leader_abilities = Counter()
    stratagems = Counter()

    deck_files = os.listdir(deck_dir)
    deck_json_files = [file for file in deck_files if file.endswith(".json")]

    for deck_file in deck_json_files:
        with open(os.path.join(deck_dir, deck_file), "r") as file:
            deck_data = json.load(file)

        leader_abilities[deck_data["Leader"]] += 1
        stratagems[deck_data["Stratagem"]] += 1

    return leader_abilities, stratagems

def print_top_leader_abilities(leader_abilities: Counter, top_n=20):
    print(f"Top {top_n} Most Common Leader Abilities:")
    for idx, (ability, count) in enumerate(leader_abilities.most_common(top_n), 1):
        print(f"{idx}. {ability}: {count} times")

def print_top_stratagems(stratagems: Counter, top_n=20):
    print(f"\nTop {top_n} Most Common Stratagems:")
    for idx, (stratagem, count) in enumerate(stratagems.most_common(top_n), 1):
        print(f"{idx}. {stratagem}: {count} times")

leader_abilities, stratagems = count_leader_abilities_and_stratagems()

In [172]:
print_top_leader_abilities(leader_abilities, top_n=36)

Top 36 Most Common Leader Abilities:
1. Tactical Decision: 47 times
2. Patricidal Fury: 44 times
3. Guerilla Tactics: 42 times
4. Arachas Swarm: 38 times
5. Carapace: 36 times
6. Overwhelming Hunger: 36 times
7. Fruits of Ysgith: 34 times
8. Imperial Formation: 34 times
9. Blood Scent: 33 times
10. Enslave: 33 times
11. Imposter: 31 times
12. Onslaught: 31 times
13. Shieldwall: 29 times
14. Imprisonment: 28 times
15. Doulbe Cross: 27 times
16. Deadeye Ambush: 27 times
17. Mahakam Forge: 26 times
18. Toussaintois Hospitality: 25 times
19. Ursine Ritual: 25 times
20. Inspired Zeal: 25 times
21. Reckless Fury: 22 times
22. Blood Money: 21 times
23. Nature's Gift: 21 times
24. Rage of the Sea: 20 times
25. Invigorate: 20 times
26. White Frost: 20 times
27. Force of Nature: 19 times
28. Lined Pockets: 17 times
29. Mobilization: 17 times
30. Congregate: 17 times
31. Call of Harmony: 16 times
32. Battle Trance: 16 times
33. Pincer Maneuver: 16 times
34. Royal Inspiration: 15 times
35. Precisi

In [156]:
print_top_stratagems(stratagems, top_n=20)


Top 20 Most Common Stratagems:
1. Crystall Skull: 240 times
2. Cursed Scroll: 227 times
3. Tactical Advantage: 186 times
4. Magic Lamp: 102 times
5. Mask of Uroboros: 86 times
6. Tiger's Eye: 62 times
7. Urn of Shadows: 30 times
8. Collar: 20 times
9. Enchanted Armor: 17 times
10. Aen Seidhe Saber: 13 times
11. Ceremonial Dagger: 9 times
12. Basilisk Venom: 4 times
13. Engineering Solution: 4 times


In [176]:
from src.display import print_random_deck
from src.models.card import Card
from src.models.faction import get_factions
from src.models.constraints import check_constraints

decks_path = "data/decks"
deck_files = os.listdir(decks_path)
deck_json_files = [file for file in deck_files if file.endswith(".json")]
random_deck_file = random.choice(deck_json_files)

deck = []

with open(os.path.join(decks_path, random_deck_file), "r") as file:
    deck_data = json.load(file)

leader_name = deck_data["Leader"]
print(f"Leader: {leader_name}")
# print(f"Stratagem: {deck_data['Stratagem']}")

for card_entry in deck_data["Cards"]:
    card_id = card_entry["id"]
    count = card_entry["count"]
    card_info = card_df.loc[card_id]
    for _ in range(count):
        deck.append(Card(
            id=card_id,
            name=card_info["name"],
            provision=card_info["provision"],
            group=card_info["group"],
            type=card_info["type"],
            faction=card_info["faction"],
            secondary_faction=card_info["secondary_faction"],
        ))

deck = sorted(deck, key=lambda x: x.provision, reverse = True)

for card in deck:
    print(f"  - {card}")

print(f"-------------- deck len: {len(deck)} ")

factions = get_factions()
faction = next((f for f in factions if leader_name in f.leader_abilities), None)

if faction is None:
    print("Faction not found for leader ability")
else:
    result = check_constraints(deck, faction, leader_name)
    print("Deck is valid" if result else "Deck is invalid")

Leader: Imprisonment
  - Battle Stations! (Prov: 13)
  - The Mushy Truffle (Prov: 11)
  - Roach (Prov: 9)
  - Vilgefortz (Prov: 9)
  - Xarthisius (Prov: 9)
  - Royal Decree (Prov: 9)
  - Triss Merigold (Prov: 8)
  - Yennefer: Divination (Prov: 8)
  - Gascon (Prov: 8)
  - Knickers (Prov: 8)
  - One-Eyed Betsy (Prov: 8)
  - Menno Coehoorn (Prov: 7)
  - Cutthroat (Prov: 5)
  - Cutthroat (Prov: 5)
  - Iron Falcon Knife Juggler (Prov: 5)
  - Iron Falcon Knife Juggler (Prov: 5)
  - Highwayman (Prov: 5)
  - Highwayman (Prov: 5)
  - Caravan Vanguard (Prov: 5)
  - Illusionist (Prov: 5)
  - Illusionist (Prov: 5)
  - Strays of Spalla (Prov: 4)
  - Strays of Spalla (Prov: 4)
  - Iron Falcon Footman (Prov: 4)
  - Iron Falcon Footman (Prov: 4)
-------------- deck len: 25 
Provision limit exceeded
Deck is invalid


In [158]:
def fitness(deck: list[int], cooccurrence_matrix: pd.DataFrame, card_frequency: dict) -> float:
    """
    Calculates the co-occurrence fitness score of a deck based on the co-occurrence matrix and the frequency
    of each card in the deck. The fitness score is influenced by both co-occurrence between card pairs 
    and the number of times each card appears in the deck.

    Args:
        deck (list[int]): A list of card IDs in the deck.
        cooccurrence_matrix (pd.DataFrame): A symmetric DataFrame where entry (i, j) indicates the co-occurrence 
                                            frequency between card i and card j.
        card_frequency (dict): A dictionary containing the frequency of each card in the deck, with card ID as the key.

    Returns:
        float: A score representing the sum of co-occurrence frequencies for all unique card pairs in the deck,
               weighted by the frequency of each card in the deck.
    """
    score = 0
    for i in range(len(deck)):
        card_i = deck[i]
        card_i_count = card_frequency.get(card_i, 0)  # Number of times card_i appears in the deck
        score += card_i_count * 10
        for j in range(i + 1, len(deck)):
            card_j = deck[j]
            # card_j_count = card_frequency.get(card_j, 0)  # Number of times card_j appears in the deck
            
            # Add co-occurrence value weighted by the frequency of both cards
            if card_i in cooccurrence_matrix.index and card_j in cooccurrence_matrix.columns:
                score += cooccurrence_matrix.loc[card_i, card_j]

        

    return score


In [177]:
deck_scores = []

deck_files = os.listdir(decks_path)
deck_json_files = [file for file in deck_files if file.endswith(".json")]

for deck_file in deck_json_files:
    with open(os.path.join(decks_path, deck_file), "r") as file:
        deck_data = json.load(file)

    card_ids = []
    for card_entry in deck_data["Cards"]:
        card_ids.extend([card_entry["id"]] * card_entry["count"])

    score = fitness(card_ids, cooccurrence_matrix, normalized_occurrences)
    deck_scores.append((deck_file, score))

# Sort decks by score descending and print top 10
top_decks = sorted(deck_scores, key=lambda x: x[1], reverse=True)[::-1][:50]

print("Top 10 Decks by Fitness Score:")
for filename, score in top_decks:
    with open(os.path.join(decks_path, filename), "r") as file:
        deck_data = json.load(file)

    print(f"\nDeck: {filename} | Fitness Score: {score}")
    print(f"Leader: {deck_data['Leader']}")
    print(f"Stratagem: {deck_data['Stratagem']}")
    cards_with_info = []
    for card in deck_data["Cards"]:
        card_id = card["id"]
        count = card["count"]
        card_info = card_df.loc[card_id]
        cards_with_info.append((card_info["provision"], card_info["name"], count))

    cards_with_info.sort(reverse=True)

    print("Cards:")
    for provision, name, count in cards_with_info:
        print(f" - {name} (Provision: {provision}) x{count}")


Top 10 Decks by Fitness Score:

Deck: 554.json | Fitness Score: 134.61772650981143
Leader: Jackpot
Stratagem: Crystall Skull
Cards:
 - Novigrad (Provision: 13) x1
 - Geralt: Professional (Provision: 11) x1
 - Living Armor (Provision: 10) x1
 - Colossal Ifrit (Provision: 10) x1
 - Allgod (Provision: 10) x1
 - Salamander (Provision: 9) x1
 - Whoreson Senior (Provision: 8) x1
 - Bart (Provision: 8) x1
 - Avallac'h: Sage (Provision: 8) x1
 - Prince Villem (Provision: 6) x1
 - Pickpocket (Provision: 6) x1
 - Mercenary Contract (Provision: 6) x1
 - Adalbertus Kalkstein (Provision: 6) x1
 - Treasure Huntress (Provision: 5) x1
 - Thunderbolt (Provision: 5) x1
 - Salamandra Mage (Provision: 5) x1
 - Firesworn Scribe (Provision: 5) x1
 - Crownsplitter Thug (Provision: 5) x1
 - Passiflora Peaches (Provision: 4) x1
 - Ofiri Merchant (Provision: 4) x1
 - Impenetrable Fog (Provision: 4) x1
 - Fortune Teller (Provision: 4) x1
 - Elder Bear (Provision: 4) x1
 - Beggar (Provision: 4) x1
 - Arena Ghoul 